In [ ]:
import pandas as pd
from os import environ
from dotenv import load_dotenv
from langchain.prompts import PromptTemplate
from langchain_mistralai import MistralAIEmbeddings
from langchain_core.pydantic_v1 import BaseModel, Field
from langchain_community.chat_models import ChatAnyscale
from langchain.output_parsers import PydanticOutputParser
from langchain_experimental.text_splitter import SemanticChunker

load_dotenv()


In [ ]:
class SVOTriple(BaseModel):
    """
    Represents a subject-verb-object triple in a sentence.

    Attributes:
        subject (str): The subject of the sentence.
        verb (str): The verb of the sentence.
        object (str): The object of the sentence.
    """

    subject: str = Field(description="The subject of the sentence")
    verb: str = Field(description="The verb of the sentence")
    object: str = Field(description="The object of the sentence")


class SVOTripleList(BaseModel):
    """
    Represents a list of Subject-Verb-Object (SVO) triples.
    """

    triples: list[SVOTriple] = Field(description="List of SVO triples")


In [ ]:
model = ChatAnyscale(
    anyscale_api_key=environ["ANYSCALE_API_KEY"],
    model_name="mistralai/Mixtral-8x7B-Instruct-v0.1",
    temperature=0,
    max_tokens=4096,
)

embeddings = MistralAIEmbeddings(
    mistral_api_key=environ["MISTRAL_API_KEY"],
)

text_splitter = SemanticChunker(embeddings)


In [ ]:
with open("./patanjali/the-yoga-sutras.md") as file:
    contents = file.read()

docs = text_splitter.create_documents([contents])


In [ ]:
template = """You are an expert entity extractor that always maintains as much semantic meaning as possible. You use inference or deduction whenever necessary to supply missing or omitted data. Examine the provided data, text, or information and generate a list of any entities or objects that match the requested format.
# Additional Instructions
1. Carefully read the provided data, text, or information to understand the context and the dynamics between entities.
2. Identify all subjects, verbs, and objects within the sentences, keeping an eye out for complex sentences that might contain multiple entities or actions.
3. Extract all Subject-Verb-Object (SVO) triples from each sentence or statement. Ensure to include all possible combinations in sentences with multiple subjects, verbs, or objects, creating separate triples for each variation.
4. When you encounter pronouns (e.g., he, she, they) or other words that do not clearly name an entity but refer to one mentioned in the text, substitute the pronoun or vague term with the correct, specific name of the entity it refers to. Use the context provided in the text to accurately determine to which entity the pronoun or term is referring. For example, if a sentence says "They offer great value," and "they" refers to "The new smartphones launched," then replace "they" with "The new smartphones launched" in your SVO triple.
5. If a sentence contains conjunctions like "and" or "or" that link subjects, verbs, or objects, split these into separate entities for your SVO triples.
6. Use your inference skills to complete the triples when the sentence structure is implicit, or some SVO parts are omitted but can be inferred from the context. This includes continuing to utilize specific names for entities rather than pronouns when the subject or object refers back to something previously mentioned.
7. In the case of compound verbs or objects where a series of actions or objects are listed for a single subject, create a distinct triple for each action or object linked to the subject. 
8. Consider indirect objects or prepositional phrases as part of the object in your SVO triples if they add significant meaning to the overall action described.
9. For verbs that are part of phrasal verbs or require prepositions to convey the full meaning (e.g., "look after"), include these as part of the verb in your SVO triple.
10. Double-check your list of triples to ensure comprehensiveness and accuracy, especially in dense or complex paragraphs that may contain multiple actions and entities interacting.
# Response format
{response_format}
# Data to extract
```
{data}
```
"""

parser = PydanticOutputParser(pydantic_object=SVOTripleList)

prompt = PromptTemplate(
    template=template,
    input_variables=["data"],
    partial_variables={"response_format": parser.get_format_instructions()},
)

chain = prompt | model | parser


In [ ]:
output = []

for doc in docs:
    try:
        result = chain.invoke({"data": data})
    except Exception as e:
        print("Error in processing document:", e)
        print("Retrying")
        try:
            result = chain.invoke({"data": data})
        except Exception as e:
            print("Error in processing document:", e)
            continue
    output.append(result)


In [ ]:
import pickle

with open("patanjali_svo.pkl", "wb") as file:
    pickle.dump(output, file)


In [ ]:
data = [triple.dict() for svo_list in output for triple in svo_list.triples]

df = pd.DataFrame(data)


In [ ]:
df.to_csv("patanjali_svo.csv", index=False)


In [ ]:
import networkx as nx

G = nx.DiGraph()

for index, row in df.iterrows():
    subject = row["subject"]
    verb = row["verb"]
    obj = row["object"]

    if not G.has_node(subject):
        G.add_node(subject)
    if not G.has_node(obj):
        G.add_node(obj)

    G.add_edge(subject, obj, label=verb)


In [ ]:
import matplotlib.pyplot as plt

nx.draw(G, with_labels=True)
plt.show()


In [ ]:
from networkx import write_gexf

write_gexf(G, "patanjali_svo.gexf")
